In [46]:
import pandas as pd
import numpy as np
import plotly.express as px

# Definir o código da estação
codigo_estacao = '86100600'

# Construir o caminho do arquivo dinamicamente
file_path = f'dados_estacao_detalhada_{codigo_estacao}_consolidado_ALL.csv'

# Carregar o arquivo CSV correspondente ao código da estação
df = pd.read_csv(file_path)

# Converter a coluna 'Data_Hora_Medicao' para datetime
df['Data_Hora_Medicao'] = pd.to_datetime(df['Data_Hora_Medicao'], errors='coerce')

# Filtrar a partir de 01/01/2019
df = df[df['Data_Hora_Medicao'] >= '2019-01-01']

# Filtrar apenas os horários cheios (minuto == 00)
df = df[df['Data_Hora_Medicao'].dt.minute == 0]

# Definir o intervalo de tempo desejado de 1 em 1 hora
date_range = pd.date_range(start=df['Data_Hora_Medicao'].min(),
                           end=df['Data_Hora_Medicao'].max(),
                           freq='H')

# Criar um DataFrame vazio com o intervalo de 1 em 1 hora
df_full_range = pd.DataFrame(date_range, columns=['Data_Hora_Medicao'])

# Mesclar seus dados existentes com o novo DataFrame de intervalo de tempo
#df_merged = pd.merge(df_full_range, df[['Data_Hora_Medicao', 'Chuva_Adotada']], on='Data_Hora_Medicao', how='left')
df_merged = pd.merge(df_full_range, df, on='Data_Hora_Medicao', how='left')

# Marcar valores negativos como NaN para tratá-los como dados faltantes
df_merged.loc[df_merged['Chuva_Adotada'] < 0, 'Chuva_Adotada'] = np.nan

# Relatório inicial de dados faltantes
total_rows = df_merged.shape[0]
missing_data_count = df_merged['Chuva_Adotada'].isnull().sum()
missing_data_percent = (missing_data_count / total_rows) * 100

report_df = pd.DataFrame({
    'Total': [total_rows],
    'Total_Faltantes': [missing_data_count],
    'Percentual_Faltantes (%)': [missing_data_percent],
})

print("Relatório inicial de dados faltantes:")
print(report_df)

# Gráfico da série temporal de 'Chuva_Adotada'
#fig = px.bar(df_merged, x='Data_Hora_Medicao', y='Chuva_Adotada', title='Chuva_Adotada - Valores Originais')
fig = px.line(df_merged, x='Data_Hora_Medicao', y='Chuva_Adotada', title='Chuva_Adotada - Valores Originais')
fig.update_layout(xaxis_title='Data', yaxis_title='Chuva (mm)')
fig.show()

# Salvar o gráfico em arquivo HTML
fig.write_html(f'{codigo_estacao}Chuva_Adotada_valores_originais.html')


C:\Users\fabri\AppData\Local\Temp\ipykernel_8404\2014158446.py:12: DtypeWarning:

Columns (14) have mixed types. Specify dtype option on import or set low_memory=False.



Relatório inicial de dados faltantes:
   Total  Total_Faltantes  Percentual_Faltantes (%)
0  45732              613                  1.340418


## Preenche dados faltante com 0

In [47]:
# Preencher valores faltantes em 'Chuva_Adotada' com zero
df_merged['Chuva_Adotada'].fillna(0, inplace=True)

# Verificar se ainda há valores faltantes após preenchimento
missing_data_after_fill = df_merged['Chuva_Adotada'].isnull().sum()
print(f"Dados faltantes após preencher com zeros: {missing_data_after_fill}")
print(df_merged['Chuva_Adotada'].describe())


Dados faltantes após preencher com zeros: 0
count    45732.000000
mean         0.189342
std          1.173991
min          0.000000
25%          0.000000
50%          0.000000
75%          0.000000
max         48.600000
Name: Chuva_Adotada, dtype: float64


In [48]:
# Histograma da coluna 'Chuva_Adotada'
fig_hist = px.histogram(df_merged, x='Chuva_Adotada', nbins=100, 
                        title='Distribuição de Chuva_Adotada',
                        labels={'Chuva_Adotada': 'Chuva (mm)'})
fig_hist.update_layout(xaxis_title='Chuva (mm)', yaxis_title='Frequência')
fig_hist.show()

# Salvar o histograma em arquivo HTML
#fig_hist.write_html('Chuva_Adotada_histograma.html')

# Boxplot da coluna 'Chuva_Adotada'
fig_box = px.box(df_merged, y='Chuva_Adotada', 
                title='Boxplot de Chuva_Adotada',
                labels={'Chuva_Adotada': 'Chuva (mm)'})
fig_box.show()

# Salvar o boxplot em arquivo HTML
#fig_box.write_html('Chuva_Adotada_boxplot.html')


In [49]:
import numpy as np
import plotly.express as px

# Definir limites físicos para precipitação
limite_superior = 58  # mm
limite_inferior = 0   # mm

# Substituir valores fora dos limites por 0 no df_merged
df_merged['Chuva_Adotada'] = df_merged['Chuva_Adotada'].apply(
    lambda x: 0 if x > limite_superior or x < limite_inferior else x)

# Plotar gráfico após o tratamento
fig = px.line(df_merged, x='Data_Hora_Medicao', y='Chuva_Adotada',
              title='Chuva_Adotada Após Tratamento de Anomalias com Limites Físicos')
fig.show()

# Salvar o gráfico em arquivo HTML
fig.write_html(f'{codigo_estacao}_Chuva_Adotada_tratamento_anomalias.html')

# Salvar o DataFrame tratado em arquivo CSV
df_merged.to_csv(f'{codigo_estacao}_chuva_adotada_FINAL.csv', index=False)

# Imprimir um relatório final da coluna 'Chuva_Adotada'
print(df_merged['Chuva_Adotada'].describe())


count    45732.000000
mean         0.189342
std          1.173991
min          0.000000
25%          0.000000
50%          0.000000
75%          0.000000
max         48.600000
Name: Chuva_Adotada, dtype: float64
